In [1]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm

### Tree and dataframe setup

In [2]:
# generate a random tree
NSPECIES = 80
TREE = toytree.rtree.bdtree(
    ntips=NSPECIES,
    seed=666,
).mod.node_scale_root_height(1.0)

# node idxs that delimit several distinct clades on this tree
CLADES = [152, 153, 154, 155]

# draw and color the four major clades
TREE.draw(
    layout='d', 
    width=500,
    tip_labels=False,
    edge_colors=TREE.get_edge_values_mapped({
        j: toytree.colors[i] for i, j in enumerate(CLADES)
    }),
    scalebar=True,
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tbaeb1a9d141a428bb6c4f0877d18484a" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0

In [3]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in CLADES}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])

In [4]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 3.0
𝛽_std = 0.2
𝜓_mean = 0.0
𝜓_std = 0.33

# 4 different clade effects on rate of RI (used for partial-pooling data)
𝜓_0_mean = 1.0
𝜓_0_std = 0.1
𝜓_1_mean = 0.5
𝜓_1_std = 0.05
𝜓_2_mean = -0.5
𝜓_2_std = 0.05
𝜓_3_mean = -1.0
𝜓_3_std = 0.1

In [5]:
# species dataframe
SPECIES_DATA = pd.DataFrame({
    "gidx": gidx,
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_0_mean, 𝜓_0_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_1_mean, 𝜓_1_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_2_mean, 𝜓_2_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_3_mean, 𝜓_3_std, len(gidx[gidx == 3])),
    ]),
})
SPECIES_DATA.head()

gidx         b       psi     psi_x
0     0  2.570468 -0.236524  0.997529
1     0  3.292698 -0.624017  0.863576
2     0  2.936227 -0.612795  0.956139
3     0  2.746916 -0.234236  1.115301
4     0  2.767121  0.031270  0.981499

### Generate crossing data

In [12]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(NSPECIES), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [(get_dist(TREE, i, j) / 2) for (i, j) in zip(a, b)],
})

DATA['b'] = np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)
DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)
DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])
# DATA['error'] = np.random.normal(0.0, 𝜎_std, DATA.shape[0])

# get logits
DATA['logit_b'] = (
        1 / (1 + np.exp(-(1 - (1 - DATA.intercept) * np.exp(-DATA.b * DATA.dist))))
)
DATA['logit'] = (
        1 / (1 + np.exp(-(1 - (1 - DATA.intercept) * np.exp(-DATA.velo * DATA.dist))))
)
DATA['logit_x'] = (
        1 / (1 + np.exp(-(1 - (1 - DATA.intercept) * np.exp(-DATA.velo_x * DATA.dist))))
)

# get RI estimates
DATA['RI_pooled'] = np.random.binomial(n=1, p=DATA.logit_b / DATA.logit_b.max())
DATA['RI_unpooled'] = np.random.binomial(n=1, p=DATA.logit / DATA.logit.max())
DATA['RI_partpooled'] = np.random.binomial(n=1, p=DATA.logit_x / DATA.logit_x.max())

DATA.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0      0      1  0.073376  3.050238  2.189697  4.911342   0.088456  0.567401   
1      0      2  0.089748  2.934435  2.085116  4.888103   0.066720  0.570234   
2      0      3  0.129770  3.050925  2.580165  5.163755   0.060944  0.590965   
3      0      4  0.144542  2.734274  2.529021  4.713303   0.028595  0.585581   
4      0      5  0.144542  2.586963  2.832430  4.665510   0.026568  0.581821   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.555707  0.590075          0            1              1  
1  0.556261  0.598243          0            1              1  
2  0.581307  0.627037          1            0              1  
3  0.580792  0.624454          1            1              1  
4  0.587490  0.623412          1            1              1

In [13]:
NSAMPLES = 2000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0      7     40  0.742448  3.142599  2.117694  4.666412   0.040860  0.712382   
1     15     64  1.000000  3.095601  2.373652  3.712292   0.042259  0.722453   
2      1      3  0.129770  2.967171  2.108919  4.946048   0.062343  0.589525   
3     20     23  0.341800  3.071183  3.050320  5.058531   0.074073  0.662822   
4     20     50  1.000000  2.909024  3.112485  3.306368   0.034037  0.720577   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.690169  0.725118          1            1              1  
1  0.713163  0.726435          1            1              1  
2  0.571222  0.623984          1            1              1  
3  0.662304  0.697556          1            1              1  
4  0.722526  0.724042          1            1              1

### Visualize data

In [14]:
def logit_plot(dist, logit, RI):
    canvas = toyplot.Canvas(width=500, height=250)
    ax0 = canvas.cartesian(
        label="pooled data (function)",
        xlabel="Genetic dist.",
        ylabel="Logit function",
        grid=(1, 2, 0),
    )
    ax1 = canvas.cartesian(
        label="pooled data (observation)",
        xlabel="Genetic dist.",
        ylabel="RI",
        grid=(1, 2, 1),
    )

    # points are jittered on x-axis for visibility
    ax0.scatterplot(
        dist,
        logit,
        size=5,
        opacity=0.33,
        color=toyplot.color.Palette()[0],
    );
    ax1.scatterplot(
        dist,
        RI,
        size=10,
        opacity=0.2,
        marker="|",
        mstyle={
            "stroke": toyplot.color.Palette()[1],
            "stroke-width": 3,
        },
    );
    return canvas, (ax0, ax1)

In [15]:
logit_plot(SAMPLE.dist, SAMPLE.logit_b, SAMPLE.RI_pooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t395492d8eba54f78bfe0b5abf11e99b2" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rg

In [16]:
logit_plot(SAMPLE.dist, SAMPLE.logit, SAMPLE.RI_unpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tb15b20fa1afa43928ab5ae5614ba4e52" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" sty

In [17]:
logit_plot(SAMPLE.dist, SAMPLE.logit_x, SAMPLE.RI_partpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="ta4f7f578ab0445af9a6b3411a8ee0bba" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:0.33;stroke:rgb(40%,76.1%,64.7%);stroke-opacity:1.0" transform="translate(138.9080571199085, 10

### Define models

In [18]:
def pooled_logistic(x, y, **kwargs):
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 1 - (1 -𝛼) * np.exp(-𝛽 * x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [19]:
def unpooled_logistic(x, y, idx0, idx1, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0.values)
        sidx1 = pm.Data("spp_idx1", idx1.values)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 1 - (1 -𝛼) * np.exp(-(𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [20]:
def partpooled_logistic(x, y, idx0, idx1, gidx, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0)
        sidx1 = pm.Data("spp_idx1", idx1)
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=4)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=4)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        
        # linear model prediction
        effect = 1 - (1 -𝛼) * np.exp(-(𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood (normal distributed errors)
        y = pm.Bernoulli("y", p=logit, observed=y)

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

### Functions to plot results

In [21]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [22]:
import scipy.stats as stats

def draw_velocity_dists(trace, baseline=0.15):
    """
    Draw the clade velocities as gaussians
    """
    canvas = toyplot.Canvas(width=350, height=300)
    axes = canvas.cartesian(xlabel="Relative velocity of reproductive isolation")
    marks = []
    base = 0
    for i in range(trace['𝜓_mean'].shape[1]):
        
        loc = trace['𝜓_mean'][:, i].mean()
        scale = trace['𝜓_std'][:, i].mean()
        interval = stats.norm.interval(0.995, loc, scale)
        points = np.linspace(interval[0], interval[1], 100)
        mark = axes.fill(
            points, 
            stats.norm.pdf(points, loc=loc, scale=scale), 
            style={
                "fill-opacity": 0.45,
                "stroke": 'black',
                "stroke-opacity": 1.0,
                "stroke-width": 1,
            },
            baseline=np.repeat(base, 100),
        )
        marks.append(mark)
        axes.hlines(base, style={"stroke-dasharray": "5,5", 'stroke-width': 1})
        base += baseline
        
    axes.y.show = False
    axes.x.ticks.locator = toyplot.locator.Extended(only_inside=True)
    axes.x.ticks.show = True
    return canvas, axes, marks

In [23]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=10000,
    draws=10000,
    target_accept=0.99,
    return_inferencedata=False,
    progressbar=True,
)

### Run three datasets under pooled model

In [41]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_pooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 587 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_unpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


In [35]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_partpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 511 seconds.
The number of effective samples is smaller than 25% for some parameters.


### Run three datasets under unpooled model

In [24]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_pooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 32592 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [48]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_unpooled_data  = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 32260 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [58]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_partpooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 63645 seconds.
The number of effective samples is smaller than 25% for some parameters.


### Run three datasets under partpooled model

In [52]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_pooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 25021 seconds.
There were 3 divergences after tuning. Increase `target_accept` or reparameterize.
There was 1 divergence after tuning. Increase `target_accept` or reparameterize.
The number of effective samples is smaller than 25% for some parameters.


In [55]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_unpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 18105 seconds.
There was 1 divergence after tuning. Increase `target_accept` or reparameterize.
The number of effective samples is smaller than 25% for some parameters.


In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_partpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


In [27]:
partpooled_model_partpooled_data['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  \
𝜓_mean[0]   -0.454  2.386  -5.007    3.975      0.026    0.018    8701.0   
𝜓_mean[1]   -5.532  3.468 -12.151    0.805      0.024    0.017   21125.0   
𝜓_mean[2]    1.575  2.326  -2.700    6.081      0.025    0.018    8582.0   
𝜓_mean[3]    1.797  2.330  -2.640    6.151      0.025    0.018    8566.0   
𝜓_offset[0] -0.458  0.882  -2.128    1.170      0.004    0.004   40116.0   
...            ...    ...     ...      ...        ...      ...       ...   
logit[1995]  0.993  0.013   0.970    1.000      0.000    0.000   19932.0   
logit[1996]  0.989  0.027   0.943    1.000      0.000    0.000   32749.0   
logit[1997]  0.851  0.030   0.793    0.907      0.000    0.000   34674.0   
logit[1998]  0.997  0.012   0.990    1.000      0.000    0.000   31763.0   
logit[1999]  1.000  0.001   1.000    1.000      0.000    0.000   35729.0   

              ess_sd  ess_bulk  ess_tail  r_hat  
𝜓_mean[0]     8701.0    8699.0   14194.0    1.0  
𝜓_mean[1]    21125.0   20944.0   24502.0    1.0  
𝜓_mean[2]     8582.0    8584.0   14286.0    1.0  
𝜓_mean[3]     8566.0    8569.0   14560.0    1.0  
𝜓_offset[0]  21668.0   40872.0   27546.0    1.0  
...              ...       ...       ...    ...  
logit[1995]  19660.0   13411.0   28880.0    1.0  
logit[1996]  32749.0   37440.0   32460.0    1.0  
logit[1997]  34674.0   34587.0   30563.0    1.0  
logit[1998]  31763.0   19887.0   31820.0    1.0  
logit[1999]  35704.0   33934.0   36000.0    1.0  

[2170 rows x 11 columns]

In [28]:
toytrace(partpooled_model_partpooled_data['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="tb46942eff7cd4ecbae826581ff2c9eed" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 178.62701056553144 149.83347210657783 L 181.04891593335276 149.91673605328893 L 183.4708213011741 149.83347210657783 L 185.8927266689955 150.0 L 188.31463203681687 149.91673605328893 L 190.73653740463823 149.83347210657783 L 193.15844277245958 149.83347210657783 L 195.58034814028093 149.91673605328893 L 198.0022535081023 149.50041631973355 L 200.42415887592364 149.6669442131557 L 202.846064243745 149.58368026644465 L 205.26796961156637 149.16736053288926 L 207.68987497938772 148.83430474604498 L 210.11178034720908 148.6677768526228 L 212.53368571503043 148.83430474604498 L 214.9555910828518 148.25145711906745 L 217.37749645067316 148.33472106577852 L 219.79940181849452 147.5020815986678 L 222.22130718631587 146.66944213155702 L 224.6432125541372 146.08659450457952 L 227.0651179219586 145.67027477102414 L 229.48702328977996 144.5878434637802 L 231.9089286576013 143.5054121565362 L 234.33083402542263 143.9217318900916 L 236.75273939324398 140.00832639467112 L 239.1746447610654 138.25978351373854 L 241.59655012888672 135.67860116569528 L 244.01845549670807 131.59866777685264 L 246.44036086452945 132.2647793505412 L 248.86226623235083 128.1015820149875 L 251.2841716001722 125.02081598667776 L 253.70607696799357 120.44129891756869 L 256.12798233581486 117.44379683597002 L 258.5498877036362 117.44379683597002 L 260.97179307145757 113.44712739383846 L 263.393698439279 108.20149875104079 L 265.81560380710033 106.61948376353038 L 268.2375091749217 97.71024146544546 L 270.65941454274304 97.37718567860117 L 273.0813199105644 88.38467943380516 L 275.50322527838574 86.21981681931724 L 277.9251306462071 80.72439633638635 L 280.34703601402845 73.14737718567861 L 282.76894138184986 73.64696086594503 L 285.1908467496712 69.15070774354704 L 287.6127521174925 63.738551207327234 L 290.03465748531386 63.738551207327234 L 292.4565628531352 58.32639467110741 L 294.8784682209566 54.41298917568693 L 297.300373588778 61.24063280599499 L 299.7222789565993 53.16402997502082 L 302.14418432442073 50.66611157368859 L 304.56608969224203 50.0 L 306.9879950600633 55.07910074937551 L 309.40990042788474 57.32722731057452 L 311.8318057957061 60.49125728559533 L 314.2537111635275 59.07577019150709 L 316.67561653134885 64.1548709408826 L 319.0975218991702 67.90174854288094 L 321.5194272669916 71.81515403830142 L 323.94133263481285 73.14737718567861 L 326.3632380026342 86.05328892589509 L 328.7851433704556 88.30141548709409 L 331.20704873827697 90.46627810158202 L 333.6289541060984 94.29641965029141 L 336.0508594739197 98.62614487926729 L 338.4727648417411 105.03746877601998 L 340.89467020956243 111.53205661948377 L 343.31657557738373 114.19650291423812 L 345.7384809452051 115.11240632805993 L 348.1603863130265 122.85595337218984 L 350.58229168084785 121.94004995836802 L 353.0041970486692 127.01915070774353 L 355.42610241649055 129.68359700249792 L 357.8480077843119 132.76436303080766 L 360.2699131521333 134.34637801831806 L 362.6918185199546 137.0940882597835 L 365.11372388777596 140.4246461282265 L 367.5356292555973 139.0924229808493 L 369.9575346234187 143.17235636969193 L 372.3794399912401 142.75603663613654 L 374.8013453590614 146.50291423813488 L 377.2232507268828 146.08659450457952 L 379.64515609470413 146.58617818484598 L 382.0670614625255 147.5020815986678 L 384.48896683034684 147.5020815986678 L 386.91087219816825 147.66860949208996 L 389.3327775659896 148.16819317235635 L 391.75468293381095 148.2514571190674

In [29]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toyplot.color.Palette()[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t9e992c8004e641449ba3c8db8fcbd0fe" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -6 -4 -2 0 2 ESTIMATED species velocity -1 0 1 TRUE species velocity

In [67]:
stats.linregress(partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

LinregressResult(slope=-0.19163010980992062, intercept=0.18280666821216215, rvalue=-0.5330788292998929, pvalue=3.5683334277923786e-07, stderr=0.03443729555385882)

In [30]:
draw_velocity_dists(partpooled_model_partpooled_data['trace'], baseline = 1.2);

<svg class="toyplot-canvas-Canvas" height="300.0px" id="tab515ac150f14a64bfc67340f7b4c0b2" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <polygon points="172.5477260667574,250.0 173.8351227731538,250.0 175.1225194795502,250.0 176.40991618594663,250.0 177.69731289234298,250.0 178.98470959873939,250.0 180.27210630513576,250.0 181.55950301153214,250.0 182.84689971792852,250.0 184.13429642432493,250.0 185.42169313072128,250.0 186.70908983711772,250.0 187.9964865435141,250.0 189.28388324991047,250.0 190.57127995630688,250.0 191.85867666270323,250.0 193.14607336909967,250.0 194.43347007549602,250.0 195.72086678189243,250.0 197.00826348828883,250.0 198.2956601946852,250.0 199.5830569010816,250.0 200.870453607478,250.0 202.15785031387435,250.0 203.4452470202708,250.0 204.73264372666716,250.0 206.02004043306357,250.0 207.30743713945995,250.0 208.59483384585633,250.0 209.88223055225274,250.0 211.16962725864911,250.0 212.45702396504552,250.0 213.7444206714419,250.0 215.03181737783828,250.0 216.31921408423466,250.0 217.60661079063107,250.0 218.89400749702742,250.0 220.18140420342382,250.0 221.46880090982023,250.0 222.7561976162166,250.0 224.04359432261302,250.0 225.3309910290094,250.0 226.61838773540578,250.0 227.9057844418022,250.0 229.19318114819856,250.0 230.48057785459497,250.0 231.76797456099132,250.0 233.05537126738776,250.0 234.3427679737841,250.0 235.6301646801805,250.0 236.91756138657695,250.0 238.2049580929733,250.0 239.4923547993697,250.0 240.77975150576611,250.0 242.06714821216246,250.0 243.35454491855887,250.0 244.64194162495525,250.0 245.92933833135163,250.0 247.21673503774804,250.0 248.50413174414442,250.0 249.79152845054082,250.0 251.0789251569372,250.0 252.3663218633336,250.0 253.65371856972996,250.0 254.94111527612637,250.0 256.2285119825228,250.0 257.5159086889192,250.0 258.80330539531553,250.0 260.09070210171194,250.0 261.37809880810835,250.0 262.6654955145047,250.0 263.9528922209011,250.0 265.2402889272975,250.0 266.52768563369386,250.0 267.81508234009027,250.0 269.1024790464867,250.0 270.38987575288303,250.0 271.67727245927944,250.0 272.96466916567584,250.0 274.25206587207225,250.0 275.5394625784686,250.0 276.826859284865,250.0 278.11425599126136,250.0 279.40165269765777,250.0 280.6890494040542,250.0 281.9764461104506,250.0 283.263842816847,250.0 284.5512395232434,250.0 285.8386362296397,250.0 287.1260329360361,250.0 288.4134296424325,250.0 289.7008263488289,250.0 290.9882230552253,250.0 292.27561976162167,250.0 293.5630164680181,250.0 294.8504131744145,250.0 296.13780988081083,250.0 297.42520658720724,250.0 298.71260329360365,250.0 300.0,250.0 300.0,249.75082259873335 298.71260329360365,249.70829652481487 297.42520658720724,249.65960908273453 296.13780988081083,249.6040706176241 294.8504131744145,249.5409490284657 293.5630164680181,249.4694729912033 292.27561976162167,249.3888363791529 290.9882230552253,249.29820397967077 289.7008263488289,249.19671859030956 288.4134296424325,249.08350955722491 287.1260329360361,248.9577027932973 285.8386362296397,248.81843228336442 284.5512395232434,248.66485304934997 283.263842816847,248.49615550934342 281.9764461104506,248.3115811224486 280.6890494040542,248.11043916630805 279.40165269765777,247.8921244476403 278.11425599126136,247.65613569911682 276.826859284865,247.4020943698366 275.5394625784686,247.1297634730434 274.25206587207225,246.8390661151929 272.96466916567584,246.5301032966777 271.67727245927944,246.20317054811136 270.38987575288303,245.85877294864878 269.1024790464867,245.4976380658264 267.81508234009027,245.12072636108914 266.52768563369386,244.72923862250963 265.

### Assess model fit

In [165]:
def rmse(predictions, targets):
    differences = predictions - targets                       #the DIFFERENCEs.
    differences_squared = differences ** 2                    #the SQUAREs of ^
    mean_of_differences_squared = differences_squared.mean()  #the MEAN of ^
    rmse_val = np.sqrt(mean_of_differences_squared)           #ROOT of ^
    return rmse_val   

In [166]:
def aicm(mean, variance):
    return 2*mean - 2*variance

In [167]:
rmse(unpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi'])

0.9384409617057597

In [168]:
rmse(partpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

0.6105422350829149

In [177]:
aicm(unpooled_sub['trace']['𝜓'].mean(), unpooled_sub['trace']['𝜓'].var())

-24.454868204001738

In [179]:
# Raftery et al. (2007) holds that this value is better.  R+M disagree?
aicm(partpooled_sub['trace']['𝜓'].mean(), partpooled_sub['trace']['𝜓'].var())

-12.49733802346165

In [59]:
az_pooled_model_pooled_data = az.from_pymc3(trace = pooled_model_pooled_data['trace'], 
                                            model = pooled_model_pooled_data['model'])
az_pooled_model_unpooled_data = az.from_pymc3(trace = pooled_model_unpooled_data['trace'], 
                                            model = pooled_model_unpooled_data['model'])
az_pooled_model_partpooled_data = az.from_pymc3(trace = pooled_model_partpooled_data['trace'], 
                                            model = pooled_model_partpooled_data['model'])
az_unpooled_model_pooled_data = az.from_pymc3(trace = unpooled_model_pooled_data['trace'], 
                                            model = unpooled_model_pooled_data['model'])
az_unpooled_model_unpooled_data = az.from_pymc3(trace = unpooled_model_unpooled_data['trace'], 
                                            model = unpooled_model_unpooled_data['model'])
az_unpooled_model_partpooled_data = az.from_pymc3(trace = unpooled_model_partpooled_data['trace'], 
                                            model = unpooled_model_partpooled_data['model'])
az_partpooled_model_pooled_data = az.from_pymc3(trace = partpooled_model_pooled_data['trace'], 
                                            model = partpooled_model_pooled_data['model'])
az_partpooled_model_unpooled_data = az.from_pymc3(trace = partpooled_model_unpooled_data['trace'], 
                                            model = partpooled_model_unpooled_data['model'])
az_partpooled_model_partpooled_data = az.from_pymc3(trace = partpooled_model_partpooled_data['trace'], 
                                            model = partpooled_model_partpooled_data['model'])

### Compare models with different datasets

In [60]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "pooled_model_unpooled_data": az_pooled_model_unpooled_data, 
            "pooled_model_partpooled_data": az_pooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo      weight  \
pooled_model_partpooled_data    0 -237.109   1.9807        0     0.86372   
pooled_model_pooled_data        1 -271.981  2.04825  34.8714    0.134453   
pooled_model_unpooled_data      2 -324.746  1.98683   87.637  0.00182669   

                                   se      dse warning loo_scale  
pooled_model_partpooled_data  25.5395        0   False       log  
pooled_model_pooled_data      22.0423  32.1629   False       log  
pooled_model_unpooled_data    23.6975  33.8957   False       log

In [61]:
az.compare({"unpooled_model_pooled_data": az_unpooled_model_pooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo       weight  \
unpooled_model_partpooled_data    0 -225.686  24.5486        0     0.932496   
unpooled_model_pooled_data        1 -272.939  12.8418  47.2527    0.0675038   
unpooled_model_unpooled_data      2 -324.497  14.3988  98.8109  1.20452e-07   

                                     se      dse warning loo_scale  
unpooled_model_partpooled_data  26.1506        0    True       log  
unpooled_model_pooled_data      20.4907  31.2855    True       log  
unpooled_model_unpooled_data    24.8467  32.9552    True       log

In [62]:
az.compare({"partpooled_model_pooled_data": az_partpooled_model_pooled_data,
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo       weight  \
partpooled_model_partpooled_data    0 -214.364  20.7363        0     0.975127   
partpooled_model_pooled_data        1  -277.01  27.9165   62.646    0.0248729   
partpooled_model_unpooled_data      2  -326.82  24.3588  112.456  9.93107e-14   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data  25.8016        0    True       log  
partpooled_model_pooled_data      19.6747  31.2216    True       log  
partpooled_model_unpooled_data    24.1992  32.3108    True       log

### Compare datasets with different models

In [68]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "unpooled_model_pooled_data": az_unpooled_model_pooled_data, 
            "partpooled_model_pooled_data": az_partpooled_model_pooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo     d_loo     weight  \
pooled_model_pooled_data        0 -271.981  2.04825         0   0.671252   
unpooled_model_pooled_data      1 -272.939  12.8418  0.957703   0.263447   
partpooled_model_pooled_data    2  -277.01  27.9165   5.02942  0.0653011   

                                   se      dse warning loo_scale  
pooled_model_pooled_data      23.9692        0   False       log  
unpooled_model_pooled_data    24.0242  1.18459    True       log  
partpooled_model_pooled_data  24.3929  3.86028    True       log

In [69]:
az.compare({"pooled_model_unpooled_data": az_pooled_model_unpooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo     d_loo    weight  \
unpooled_model_unpooled_data      0 -324.497  14.3988         0  0.402087   
pooled_model_unpooled_data        1 -324.746  1.98683  0.249661  0.416512   
partpooled_model_unpooled_data    2  -326.82  24.3588   2.32361  0.181402   

                                     se      dse warning loo_scale  
unpooled_model_unpooled_data    25.5573        0    True       log  
pooled_model_unpooled_data      25.4386  1.51803   False       log  
partpooled_model_unpooled_data  25.4572  2.60915    True       log

In [70]:
az.compare({"pooled_model_partpooled_data": az_pooled_model_partpooled_data,
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

rank      loo    p_loo    d_loo       weight  \
partpooled_model_partpooled_data    0 -214.364  20.7363        0     0.993501   
unpooled_model_partpooled_data      1 -225.686  24.5486  11.3216   0.00609434   
pooled_model_partpooled_data        2 -237.109   1.9807  22.7452  0.000404419   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data   23.083        0    True       log  
unpooled_model_partpooled_data    21.6275  4.35591    True       log  
pooled_model_partpooled_data      20.5098  6.68468   False       log

### other stuff

In [64]:
# Save trace.  To load in different notebook, model context and sample data is required.
pm.save_trace(partpooled_model_partpooled_data['trace'], directory = "/home/henry/oaks-thesis/trace/asymptotic-pmpd")

'/home/henry/oaks-thesis/trace/asymptotic-pmpd'

In [65]:
asymptotic_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

In [66]:
%store asymptotic_args

Stored 'asymptotic_args' (list)
